In [5]:
import pandas as pd
import json as js
from glob import glob
from sklearn.impute import SimpleImputer
import cufflinks as cornflakes

cornflakes.go_offline()

# ETL 

Creamos la funcion para el ETL, qque automatimaticamente separa lo datafrmes por ano para un mejor analisis, 
la forma del dataframe fue pensada para la alimentacion directa al modelo, y se le agregaron mas columnas para una mejor prediccion. 

### Lista de archivos json

In [6]:
files = glob("../data/historical/*.json")

### Implementacion

In [7]:

def ETL(*,files:list, columns:list = ["TMP","RH","WDR","WSP"]) -> dict:
    """Function that simulates the ETL, it crates a separated dataframe per year, 
    so we can perform a better analysis.
    it imputes the data with the median, and cast the cesasary columns to its correspondant

    Args:
        files (list): list of jsosn files to be read
        columns (list, optional): columns of the jsons to be taken. Defaults to ["TMP","RH","WDR","WSP"].

    Returns:
        dict: dictionary of dataframes with the format { year -> data }
    """    
    
    dataframes = {  }
        
    for file in files:
        
        with open(file, "r+") as f:data = js.load(f)
        
        raw_data = []
        registers = data["pollutionMeasurements"]["date"]
        emputador = SimpleImputer(strategy='median')
        
        for date in registers.keys(): 
            
            register = registers.get(date)
            raw_data.append(dict(FECHA=date, **dict( map( lambda col:(col,register.get(col).get("FAC",None)) ,columns ) )))

        auxiliar_dataframe = pd.DataFrame(raw_data)
        for column in columns: auxiliar_dataframe[column] = pd.to_numeric(auxiliar_dataframe[column], errors="coerce")
        
        auxiliar_dataframe["FECHA"]= auxiliar_dataframe["FECHA"].apply(lambda x: x[:11] + "00" + x[13:] if x[11:13] == "24" else x)
        auxiliar_dataframe["FECHA"] = pd.to_datetime(auxiliar_dataframe["FECHA"], format="mixed")
        auxiliar_dataframe = auxiliar_dataframe.sort_values(by="FECHA", inplace=False).reset_index(drop=True)
        
        imputador = emputador.fit_transform(auxiliar_dataframe[columns])
        auxiliar_dataframe[columns] = imputador

        dataframes[file.split('_')[1].replace('.json','')] = auxiliar_dataframe
        
    return dataframes

### Obtencion de los resultados

In [8]:
dataframes = ETL(files = files)

### Ejemplo de la la forma y estadisticas de uno de los dataframes

In [9]:
dataframes['2022'].head()

FECHA  TMP    RH    WDR  WSP
0 2022-01-01 00:00:00  9.2  53.0  245.0  1.0
1 2022-01-01 01:00:00  9.1  71.0  250.0  1.4
2 2022-01-01 02:00:00  8.1  75.0  252.0  1.2
3 2022-01-01 03:00:00  7.5  75.0  251.0  1.1
4 2022-01-01 04:00:00  6.6  79.0  249.0  1.3

In [10]:
dataframes['2022'].describe()

FECHA          TMP           RH          WDR          WSP
count                 8760  8760.000000  8760.000000  8760.000000  8760.000000
mean   2022-07-02 11:30:00    14.099384    53.303881   216.770091     1.736804
min    2022-01-01 00:00:00     1.400000     1.000000     0.000000     0.200000
25%    2022-04-02 05:45:00    13.900000    35.000000   122.000000     1.100000
50%    2022-07-02 11:30:00    13.900000    54.000000   249.000000     1.600000
75%    2022-10-01 17:15:00    13.900000    72.000000   307.000000     2.200000
max    2022-12-31 23:00:00    27.900000    91.000000   360.000000     5.600000
std                    NaN     3.525987    22.096037   112.716715     0.843586

## Analisis de los datos

In [12]:
for ano, df in dataframes.items():df.iplot(kind='line', x='FECHA', y='TMP', mode='lines', xTitle='Fecha', yTitle='Temperatura registrada', title=f'Serie de tiempo - Temperatura en la FES Acátlan ano {ano}')

# Ingeniera de variables

# Variable objetivo

# Limpieza de la tabla

# Regresi ́on Lineal

# Performance